# Business Data Challenge - Team 1

In [1]:
import pandas as pd
import numpy as np
import os
import s3fs
import re

Configuration de l'accès aux données

In [2]:
# Create filesystem object
S3_ENDPOINT_URL = "https://" + os.environ["AWS_S3_ENDPOINT"]
fs = s3fs.S3FileSystem(client_kwargs={'endpoint_url': S3_ENDPOINT_URL})

# Exemple sur Company 1

## Chargement données

In [3]:
BUCKET = "bdc2324-data/1"
liste_database = fs.ls(BUCKET)

In [4]:
# loop to create dataframes from liste
files_path = liste_database

client_number = files_path[0].split("/")[1]
df_prefix = "df" + str(client_number) + "_"

for i in range(len(files_path)) :
    current_path = files_path[i]
    with fs.open(current_path, mode="rb") as file_in:
        df = pd.read_csv(file_in)
        # the pattern of the name is df1xxx
        nom_dataframe = df_prefix + re.search(r'\/(\d+)\/(\d+)([a-zA-Z_]+)\.csv$', current_path).group(3)
        globals()[nom_dataframe] = df

/tmp/ipykernel_492/4081512283.py:10: DtypeWarning: Columns (1) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(file_in)


## Cleaning functions

In [5]:
def cleaning_date(df, column_name):
    """
    Nettoie la colonne spécifiée du DataFrame en convertissant les valeurs en datetime avec le format ISO8601.

    Parameters:
    - df: DataFrame
        Le DataFrame contenant la colonne à nettoyer.
    - column_name: str
        Le nom de la colonne à nettoyer.

    Returns:
    - DataFrame
        Le DataFrame modifié avec la colonne nettoyée.
    """
    df[column_name] = pd.to_datetime(df[column_name], utc = True, format = 'ISO8601')
    return df

## Preprocessing

## customer_plus

In [6]:
def preprocessing_customerplus(customerplus = None):

    customerplus_copy = customerplus.copy()
    
    # Passage en format date
    cleaning_date(customerplus_copy, 'first_buying_date')
    cleaning_date(customerplus_copy, 'last_visiting_date')
    
    # Selection des variables
    customerplus_copy.drop(['lastname', 'firstname', 'email', 'civility', 'note', 'created_at', 'updated_at', 'deleted_at', 'extra', 'reference', 'extra_field', 'identifier', 'need_reload', 'preferred_category', 'preferred_supplier', 'preferred_formula', 'zipcode', 'last_visiting_date'], axis = 1, inplace=True)
    customerplus_copy.rename(columns = {'id' : 'customer_id'}, inplace = True)

    return customerplus_copy


In [7]:
df1_customerplus_clean = preprocessing_customerplus(df1_customersplus)

## Ticket area

In [8]:
# Fonction de nettoyage et selection
def preprocessing_tickets_area(tickets = None, purchases = None, suppliers = None, type_ofs = None):
    # Base des tickets
    tickets = tickets[['id', 'purchase_id', 'product_id', 'is_from_subscription', 'type_of', 'supplier_id']]
    tickets.rename(columns = {'id' : 'ticket_id'}, inplace = True)

    # Base des fournisseurs
    suppliers = suppliers[['id', 'name']]
    suppliers.rename(columns = {'name' : 'supplier_name'}, inplace = True)

    # Base des types de billets
    type_ofs = type_ofs[['id', 'name', 'children']]
    type_ofs.rename(columns = {'name' : 'type_of_ticket_name'}, inplace = True)

    # Base des achats
    # Nettoyage de la date d'achat
    cleaning_date(purchases, 'purchase_date')
    # Selection des variables
    purchases = purchases[['id', 'purchase_date', 'customer_id']]

    # Fusions 
    # Fusion avec fournisseurs
    ticket_information = pd.merge(tickets, suppliers, left_on = 'supplier_id', right_on = 'id', how = 'inner')
    ticket_information.drop(['supplier_id', 'id'], axis = 1, inplace=True)
    
    # Fusion avec type de tickets
    ticket_information = pd.merge(ticket_information, type_ofs, left_on = 'type_of', right_on = 'id', how = 'inner')
    ticket_information.drop(['type_of', 'id'], axis = 1, inplace=True)
    
    # Fusion avec achats
    ticket_information = pd.merge(ticket_information, purchases, left_on = 'purchase_id', right_on = 'id', how = 'inner')
    ticket_information.drop(['purchase_id', 'id'], axis = 1, inplace=True)

    return ticket_information

In [9]:
df1_ticket_information = preprocessing_tickets_area(tickets = df1_tickets, purchases = df1_purchases, suppliers = df1_suppliers, type_ofs = df1_type_ofs)

/tmp/ipykernel_492/1591303091.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  tickets.rename(columns = {'id' : 'ticket_id'}, inplace = True)
/tmp/ipykernel_492/1591303091.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  suppliers.rename(columns = {'name' : 'supplier_name'}, inplace = True)
/tmp/ipykernel_492/1591303091.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  type_ofs.rename(columns = {'name' : 'type_of_ticket_name'}

In [10]:
df1_ticket_information.head()

ticket_id  product_id  is_from_subscription   supplier_name  \
0   13070859      225251                 False  vente en ligne   
1   13070860      224914                 False  vente en ligne   
2   13070861      224914                 False  vente en ligne   
3   13070862      224914                 False  vente en ligne   
4   13070863      224914                 False  vente en ligne   

  type_of_ticket_name         children             purchase_date  customer_id  
0             Atelier  pricing_formula 2018-12-28 14:47:50+00:00        48187  
1             Atelier  pricing_formula 2018-12-28 14:47:50+00:00        48187  
2             Atelier  pricing_formula 2018-12-28 14:47:50+00:00        48187  
3             Atelier  pricing_formula 2018-12-28 14:47:50+00:00        48187  
4             Atelier  pricing_formula 2018-12-28 14:47:50+00:00        48187

### KPI tickets

In [11]:
def tickets_kpi_function(tickets_information = None):
    tickets_information_copy = tickets_information.copy()
    tickets_information_copy['purchase_date_max'] = tickets_information_copy['purchase_date']
    tickets_kpi = (tickets_information_copy[['product_id', 'customer_id', 'ticket_id','supplier_name', 'purchase_date', 'purchase_date_max']]
                   .groupby(['product_id', 'customer_id'])
                   .agg({'ticket_id': 'count', 
                         'supplier_name': 'nunique',
                         'purchase_date_max' : 'max',
                         'purchase_date' : 'min'})
                   .reset_index()
                  )
    
    tickets_kpi.rename(columns = {'ticket_id' : 'nb_tickets', 
                                  'supplier_name' : 'nb_suppliers', 
                                  'purchase_date' : 'purchase_date_min'}, inplace = True)
    
    tickets_kpi['time_between_purchase'] = tickets_kpi['purchase_date_max'] - tickets_kpi['purchase_date_min']
    
    return tickets_kpi
    

In [12]:
df1_tickets_kpi = tickets_kpi_function(tickets_information = df1_ticket_information)

In [13]:
df1_tickets_kpi.head()

product_id  customer_id  nb_tickets  nb_suppliers  \
0      107310         2805           4             2   
1      110089        54355           1             1   
2      110089        54356           1             1   
3      110089        54357           1             1   
4      110089        54358           1             1   

          purchase_date_max         purchase_date_min time_between_purchase  
0 2019-06-05 14:37:13+00:00 2019-06-05 14:18:38+00:00       0 days 00:18:35  
1 2017-02-17 13:32:51+00:00 2017-02-17 13:32:51+00:00       0 days 00:00:00  
2 2017-03-02 14:36:16+00:00 2017-03-02 14:36:16+00:00       0 days 00:00:00  
3 2017-03-06 15:16:41+00:00 2017-03-06 15:16:41+00:00       0 days 00:00:00  
4 2017-03-13 16:07:27+00:00 2017-03-13 16:07:27+00:00       0 days 00:00:00

## Target area

In [14]:
def preprocessing_target_area(targets = None, target_types = None, customer_target_mappings = None):
    # Target.csv cleaning
    targets = targets[["id", "target_type_id", "name"]]
    targets.rename(columns = {'id' : 'target_id' , 'name' : 'target_name'}, inplace = True)
    
    # target_type cleaning
    target_types = target_types[["id","is_import","name"]].add_prefix("target_type_")
    
    #customer_target_mappings cleaning
    customer_target_mappings = customer_target_mappings[["id", "customer_id", "target_id"]]
    
    # Merge target et target_type
    targets_full = pd.merge(targets, target_types, left_on='target_type_id', right_on='target_type_id', how='inner')
    targets_full.drop(['target_type_id'], axis = 1, inplace=True)
    
    # Merge
    targets_full = pd.merge(customer_target_mappings, targets_full, left_on='target_id', right_on='target_id', how='inner')
    targets_full.drop(['target_id'], axis = 1, inplace=True)

    return targets_full

In [15]:
df1_target_information = preprocessing_target_area(targets = df1_targets, target_types = df1_target_types, customer_target_mappings = df1_customer_target_mappings)

/tmp/ipykernel_492/3848597476.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  targets.rename(columns = {'id' : 'target_id' , 'name' : 'target_name'}, inplace = True)


In [16]:
df1_target_information[['target_name', 'customer_id']].groupby('target_name').count().sort_values(by='customer_id', ascending=False).head()

customer_id
target_name                                          
consentement optin mediation specialisee       150000
consentement optin jeune public                149979
consentement optin b2c                         108909
Arenametrix_bascule tel vers sib                35216
consentement optout b2c                         34523

In [17]:
df1_target_information_reduced = df1_target_information[['target_name', 'customer_id']].groupby('target_name').count()
df1_target_information_reduced[df1_target_information_reduced['customer_id'] >= 1000].head()

customer_id
target_name                                       
Arenametrix_bascule tel vers sib             35216
Autres_interet_exposition                     1021
COM Inscrits NL générale (historique)        23005
Contacts_prenomsdoubles                      11643
DDCP MD Procès du Siècle                      1684

## Campaings area

In [18]:
def preprocessing_campaigns_area(campaign_stats = None, campaigns = None):
    # campaign_stats cleaning 
    campaign_stats = campaign_stats[["id", "campaign_id", "customer_id", "opened_at", "sent_at", "delivered_at"]]
    cleaning_date(campaign_stats, 'opened_at')
    cleaning_date(campaign_stats, 'sent_at')
    cleaning_date(campaign_stats, 'delivered_at')
    
    # campaigns cleaning
    campaigns = campaigns[["id", "name", "service_id", "sent_at"]].add_prefix("campaign_")
    cleaning_date(campaigns, 'campaign_sent_at')
    
    # Merge 
    campaigns_full = pd.merge(campaign_stats, campaigns, on = "campaign_id", how = "left")
    campaigns_full.drop(['campaign_id'], axis = 1, inplace=True)

    return campaigns_full

In [19]:
df1_campaigns_information = preprocessing_campaigns_area(campaign_stats = df1_campaign_stats, campaigns = df1_campaigns)

/tmp/ipykernel_492/1967867975.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[column_name] = pd.to_datetime(df[column_name], utc = True, format = 'ISO8601')
/tmp/ipykernel_492/1967867975.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[column_name] = pd.to_datetime(df[column_name], utc = True, format = 'ISO8601')
/tmp/ipykernel_492/1967867975.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value inste

In [20]:
df1_campaigns_information.head()

id  customer_id                 opened_at                   sent_at  \
0  19793       112597                       NaT 2021-03-28 16:01:09+00:00   
1  14211       113666                       NaT 2021-03-28 16:01:09+00:00   
2  13150       280561                       NaT 2021-03-28 16:00:59+00:00   
3   7073       101007 2021-03-28 18:11:06+00:00 2021-03-28 16:00:59+00:00   
4   5175       103972                       NaT 2021-03-28 16:01:06+00:00   

               delivered_at                            campaign_name  \
0 2021-03-28 16:24:18+00:00  Le Mucem chez vous, gardons le lien #22   
1 2021-03-28 16:21:02+00:00  Le Mucem chez vous, gardons le lien #22   
2 2021-03-28 16:08:45+00:00  Le Mucem chez vous, gardons le lien #22   
3 2021-03-28 16:09:47+00:00  Le Mucem chez vous, gardons le lien #22   
4 2021-03-28 16:05:03+00:00  Le Mucem chez vous, gardons le lien #22   

   campaign_service_id          campaign_sent_at  
0                  404 2021-03-27 23:00:00+00:00  
1                  404 2021-03-27 23:00:00+00:00  
2                  404 2021-03-27 23:00:00+00:00  
3                  404 2021-03-27 23:00:00+00:00  
4                  404 2021-03-27 23:00:00+00:00

In [21]:
def campaigns_kpi_function(campaigns_information = None):
    # Nombre de campagnes de mails
    nb_campaigns = campaigns_information[['customer_id', 'campaign_name']].groupby('customer_id').count().reset_index()
    nb_campaigns.rename(columns = {'campaign_name' : 'nb_campaigns'}, inplace = True)
    # Temps d'ouverture en min moyen    
    campaigns_information['time_to_open'] = campaigns_information['opened_at'] - campaigns_information['delivered_at']
    time_to_open = campaigns_information[['customer_id', 'time_to_open']].groupby('customer_id').mean().reset_index()

    # Nombre de mail ouvert    
    opened_campaign = campaigns_information[['customer_id', 'campaign_name', 'opened_at']]
    opened_campaign.dropna(subset=['opened_at'], inplace=True)
    opened_campaign = opened_campaign[['customer_id', 'campaign_name']].groupby('customer_id').count().reset_index()
    opened_campaign.rename(columns = {'campaign_name' : 'nb_campaigns_opened' }, inplace = True)

    # Fusion des indicateurs
    campaigns_reduced = pd.merge(nb_campaigns, opened_campaign, on = 'customer_id', how = 'left')
    campaigns_reduced = pd.merge(campaigns_reduced, time_to_open, on = 'customer_id', how = 'left')

    # Remplir les NaN : nb_campaigns_opened
    campaigns_reduced['nb_campaigns_opened'].fillna(0, inplace=True)

    # Remplir les NaT : time_to_open (??)

    return campaigns_reduced
    

In [22]:
df1_campaigns_kpi = campaigns_kpi_function(campaigns_information = df1_campaigns_information) 

/tmp/ipykernel_492/3700263836.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  opened_campaign.dropna(subset=['opened_at'], inplace=True)


In [23]:
df1_campaigns_kpi.head()

customer_id  nb_campaigns  nb_campaigns_opened              time_to_open
0            2             4                  0.0                       NaT
1            3           222                124.0 1 days 00:28:30.169354838
2            4             7                  7.0 1 days 04:31:01.428571428
3            5             4                  0.0                       NaT
4            6            20                  0.0                       NaT

## Create Products Table

Some useful functions

In [24]:
BUCKET = "bdc2324-data"
directory_path = '1'

In [25]:
def display_databases(file_name):
    """
    This function returns the file from s3 storage
    """
    file_path = BUCKET + "/" + directory_path + "/" + file_name
    print("File path : ", file_path)
    with fs.open(file_path, mode="rb") as file_in:
        df = pd.read_csv(file_in, sep=",")
        
    print("Shape : ", df.shape)
    return df


def remove_horodates(df):
    """
    this function remove horodate columns like created_at and updated_at
    """
    df = df.drop(columns = ["created_at", "updated_at"])
    return df


def order_columns_id(df):
    """
    this function puts all id columns at the beginning in order to read the dataset easier
    """
    substring = 'id'
    id_columns = [col for col in df.columns if substring in col]
    remaining_col = [col for col in df.columns if substring not in col]
    new_order = id_columns + remaining_col
    return df[new_order]


def process_df_2(df):
    """
    This function organizes dataframe
    """
    df = remove_horodates(df)
    print("Number of columns : ", len(df.columns))
    df = order_columns_id(df)
    print("Columns : ", df.columns)
    return df

def load_dataset(name):
    """
    This function loads csv file
    """
    df = display_databases(name)
    df = process_df_2(df)
    # drop na :
    #df = df.dropna(axis=1, thresh=len(df))
    # if identifier in table : delete it
    if 'identifier' in df.columns:
        df = df.drop(columns = 'identifier')
    return df

Create theme tables

In [26]:
def create_products_table():
    # first merge products and categories
    print("first merge products and categories")
    products = load_dataset("1products.csv")
    categories = load_dataset("1categories.csv")
    # Drop useless columns
    products = products.drop(columns = ['apply_price', 'extra_field', 'amount_consumption'])
    categories = categories.drop(columns = ['extra_field', 'quota'])

    #Merge
    products_theme = products.merge(categories, how = 'left', left_on = 'category_id',
                                    right_on = 'id', suffixes=('_products', '_categories'))
    products_theme = products_theme.rename(columns = {"name" : "name_categories"})
    
    # Second merge products_theme and type of categories
    print("Second merge products_theme and type of categories")
    type_of_categories = load_dataset("1type_of_categories.csv")
    type_of_categories = type_of_categories.drop(columns = 'id')
    products_theme = products_theme.merge(type_of_categories, how = 'left', left_on = 'category_id',
                                          right_on = 'category_id' )

    # Index cleaning
    products_theme = products_theme.drop(columns = ['id_categories'])
    products_theme  = order_columns_id(products_theme)
    return products_theme


def create_events_table():
    # first merge events and seasons : 
    print("first merge events and seasons : ")
    events = load_dataset("1events.csv")
    seasons = load_dataset("1seasons.csv")

    # Drop useless columns
    events = events.drop(columns = ['manual_added', 'is_display'])
    seasons = seasons.drop(columns = ['start_date_time'])
        
    events_theme = events.merge(seasons, how = 'left', left_on = 'season_id', right_on = 'id', suffixes=('_events', '_seasons'))

    # Secondly merge events_theme and event_types
    print("Secondly merge events_theme and event_types : ")
    event_types = load_dataset("1event_types.csv")
    event_types = event_types.drop(columns = ['fidelity_delay'])
    
    events_theme = events_theme.merge(event_types, how = 'left', left_on = 'event_type_id', right_on = 'id', suffixes=('_events', '_event_type'))
    events_theme = events_theme.rename(columns = {"name" : "name_event_types"})
    events_theme = events_theme.drop(columns = 'id')

    # thirdly merge events_theme and facilities
    print("thirdly merge events_theme and facilities : ")
    facilities = load_dataset("1facilities.csv")
    facilities = facilities.drop(columns = ['fixed_capacity'])
    
    events_theme = events_theme.merge(facilities, how = 'left', left_on = 'facility_id', right_on = 'id', suffixes=('_events', '_facility'))
    events_theme = events_theme.rename(columns = {"name" : "name_facilities", "id_events" : "event_id"})
    events_theme = events_theme.drop(columns = 'id')

    # Index cleaning
    events_theme = events_theme.drop(columns = ['id_seasons'])
    events_theme  = order_columns_id(events_theme)
    return events_theme


def create_representations_table():
    representations = load_dataset("1representations.csv")
    representations = representations.drop(columns = ['serial', 'open', 'satisfaction', 'is_display', 'expected_filling',
                                                     'max_filling', 'extra_field', 'start_date_time', 'end_date_time', 'name',
                                                     'representation_type_id'])
    
    representations_capacity = load_dataset("1representation_category_capacities.csv")
    representations_capacity = representations_capacity.drop(columns = ['expected_filling', 'max_filling'])

    representations_theme = representations.merge(representations_capacity, how='left',
                                                  left_on='id', right_on='representation_id',
                                                  suffixes=('_representation', '_representation_cap'))
    # index cleaning
    representations_theme = representations_theme.drop(columns = ["id_representation"])
    representations_theme = order_columns_id(representations_theme)
    return representations_theme

In [27]:
products_theme = create_products_table()
products_theme.head()

first merge products and categories
File path :  bdc2324-data/1/1products.csv
Shape :  (94803, 14)
Number of columns :  12
Columns :  Index(['id', 'representation_id', 'pricing_formula_id', 'category_id',
       'products_group_id', 'product_pack_id', 'identifier', 'amount',
       'is_full_price', 'apply_price', 'extra_field', 'amount_consumption'],
      dtype='object')
File path :  bdc2324-data/1/1categories.csv
Shape :  (27, 7)
Number of columns :  5
Columns :  Index(['id', 'identifier', 'name', 'extra_field', 'quota'], dtype='object')
Second merge products_theme and type of categories
File path :  bdc2324-data/1/1type_of_categories.csv
Shape :  (5, 6)
Number of columns :  4
Columns :  Index(['id', 'type_of_id', 'category_id', 'identifier'], dtype='object')


id_products  representation_id  pricing_formula_id  category_id  \
0        10682                914                 114           41   
1          478                273                 131            1   
2        20873                275                 137            1   
3       157142              82519                   9            5   
4         1341                  9                  93            1   

   products_group_id  product_pack_id  type_of_id  amount  is_full_price  \
0              10655                1         NaN     9.0          False   
1                471                1        12.0     9.5          False   
2              20825                1        12.0    11.5          False   
3             156773                1         NaN     8.0          False   
4               1175                1        12.0     8.5          False   

     name_categories  
0  indiv activité tr  
1   indiv entrées tp  
2   indiv entrées tp  
3   indiv entrées tr  
4   indiv entrées tp

In [28]:
events_theme= create_events_table()
events_theme.head()

first merge events and seasons : 
File path :  bdc2324-data/1/1events.csv
Shape :  (1232, 12)
Number of columns :  10
Columns :  Index(['id', 'season_id', 'facility_id', 'event_type_id', 'event_type_key_id',
       'facility_key_id', 'identifier', 'name', 'manual_added', 'is_display'],
      dtype='object')
File path :  bdc2324-data/1/1seasons.csv
Shape :  (13, 6)
Number of columns :  4
Columns :  Index(['id', 'identifier', 'name', 'start_date_time'], dtype='object')
Secondly merge events_theme and event_types : 
File path :  bdc2324-data/1/1event_types.csv
Shape :  (9, 6)
Number of columns :  4
Columns :  Index(['id', 'fidelity_delay', 'identifier', 'name'], dtype='object')
thirdly merge events_theme and facilities : 
File path :  bdc2324-data/1/1facilities.csv
Shape :  (2, 7)
Number of columns :  5
Columns :  Index(['id', 'street_id', 'identifier', 'name', 'fixed_capacity'], dtype='object')


event_id  season_id  facility_id  event_type_id  event_type_key_id  \
0       192         16            1              4                  4   
1     30329       2767            1              5                  5   
2       161         16            1              2                  2   
3      5957        582            1              4                  4   
4      8337        582            1              4                  4   

   facility_key_id  street_id  \
0                1          1   
1                1          1   
2                1          1   
3                1          1   
4                1          1   

                                        name_events name_seasons  \
0                                        frontières         2018   
1  visite guidée une autre histoire du monde (1h00)         2023   
2           visite contée les chercheurs d'or indiv         2018   
3     we dreamt of utopia and we woke up screaming.         2021   
4                             jeff koons épisodes 4         2021   

           name_event_types name_facilities  
0          spectacle vivant           mucem  
1      offre muséale groupe           mucem  
2  offre muséale individuel           mucem  
3          spectacle vivant           mucem  
4          spectacle vivant           mucem

In [29]:
representation_theme = create_representations_table()
representation_theme.head()

File path :  bdc2324-data/1/1representations.csv
Shape :  (36095, 16)
Number of columns :  14
Columns :  Index(['id', 'event_id', 'representation_type_id', 'identifier', 'serial',
       'start_date_time', 'open', 'satisfaction', 'end_date_time', 'name',
       'is_display', 'expected_filling', 'max_filling', 'extra_field'],
      dtype='object')
File path :  bdc2324-data/1/1representation_category_capacities.csv
Shape :  (65241, 7)
Number of columns :  5
Columns :  Index(['id', 'representation_id', 'category_id', 'expected_filling',
       'max_filling'],
      dtype='object')


event_id  id_representation_cap  representation_id  category_id
0     12384                 123058              84820            2
1        37                   2514                269            2
2        37                    384                269            5
3        37                   2515                269           10
4        37                    383                269            1

Create uniform product database 

In [30]:
def uniform_product_df():
    """
    This function returns the uniform product dataset
    """
    print("Products theme columns : ", products_theme.columns)
    print("\n Representation theme columns : ", representation_theme.columns)
    print("\n Events theme columns : ", events_theme.columns)

    products_global = products_theme.merge(representation_theme, how='left',
                                           on= ["representation_id", "category_id"])
    
    products_global = products_global.merge(events_theme, how='left', on='event_id',
                                            suffixes = ("_representation", "_event"))
    
    products_global = order_columns_id(products_global)

    # remove useless columns 
    products_global = products_global.drop(columns = ['type_of_id', 'name_events', 'name_seasons', 'name_categories'])
    return products_global

In [31]:
products_global = uniform_product_df()
products_global.head()

Products theme columns :  Index(['id_products', 'representation_id', 'pricing_formula_id', 'category_id',
       'products_group_id', 'product_pack_id', 'type_of_id', 'amount',
       'is_full_price', 'name_categories'],
      dtype='object')

 Representation theme columns :  Index(['event_id', 'id_representation_cap', 'representation_id',
       'category_id'],
      dtype='object')

 Events theme columns :  Index(['event_id', 'season_id', 'facility_id', 'event_type_id',
       'event_type_key_id', 'facility_key_id', 'street_id', 'name_events',
       'name_seasons', 'name_event_types', 'name_facilities'],
      dtype='object')


id_products  representation_id  pricing_formula_id  category_id  \
0        10682                914                 114           41   
1          478                273                 131            1   
2        20873                275                 137            1   
3       157142              82519                   9            5   
4         1341                  9                  93            1   

   products_group_id  product_pack_id  event_id  id_representation_cap  \
0              10655                1       132                   8789   
1                471                1        37                    390   
2              20825                1        37                    395   
3             156773                1     12365                 120199   
4               1175                1         8                     21   

   season_id  facility_id  event_type_id  event_type_key_id  facility_key_id  \
0          4            1              2                  5                1   
1          2            1              2                  2                1   
2          2            1              2                  2                1   
3       1754            1              2                  4                1   
4          4            1              3                  6                1   

   street_id  amount  is_full_price          name_event_types name_facilities  
0          1     9.0          False  offre muséale individuel           mucem  
1          1     9.5          False  offre muséale individuel           mucem  
2          1    11.5          False  offre muséale individuel           mucem  
3          1     8.0          False  offre muséale individuel           mucem  
4          1     8.5          False                non défini           mucem

In [32]:
# Fusion liée au product
df1_products_purchased = pd.merge(df1_ticket_information, products_global, left_on = 'product_id', right_on = 'id_products', how = 'inner')

# Fusion des bases locales

In [33]:
# Fusion avec KPI liés au customer
df1_customer = pd.merge(df1_customerplus_clean, df1_campaigns_kpi, on = 'customer_id', how = 'left')

In [34]:
# Fusion avec KPI liés au comportement d'achat
# df1_customer_product = pd.merge(df1_customer, df1_products_purchased, on = 'customer_id', how = 'left')